* set random seed
* pre-trained models eg. Inception, EfficientNet


In [6]:
!pip3 install opencv-python

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 35.4/35.4 MB 1.6 MB/s eta 0:00:0000:0100:010m

[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python3.11 -m pip install --upgrade pip


In [1]:
import tensorflow as tf
from tensorflow import keras
import matplotlib.pyplot as plt
# %matplotlib inline
import numpy as np
import seaborn as sn
import pathlib
import cv2
import os
from os import listdir
import glob
from PIL import Image

In [3]:
from tensorflow import keras

In [6]:
cinic_directory_train = './cinic-10_image_classification_challenge-dataset/train/'
cinic_directory_test = './cinic-10_image_classification_challenge-dataset/test/'

class_name = []
file_name='output_fromKeras.csv'
optimiser='adamax' # les best : Adam, nadam et adamax
nb_epochs=50
batch_size_choice=16
image_size=(32, 32)
loss_func='sparse_categorical_crossentropy'

In [7]:
# loading in the data 
train_ds = keras.preprocessing.image_dataset_from_directory(
    cinic_directory_train,
    validation_split=0.2,
    subset="training",
    seed=1337,
    image_size=image_size,
    batch_size=batch_size_choice
)

Found 90000 files belonging to 10 classes.
Using 72000 files for training.


In [9]:
# loading in the data 
validation_ds = keras.preprocessing.image_dataset_from_directory(
    cinic_directory_train,
    validation_split=0.2,
    subset="validation",
    seed=1337,
    image_size=image_size,
    batch_size=batch_size_choice
)

Found 90000 files belonging to 10 classes.
Using 18000 files for validation.


In [39]:
class_names= train_ds.class_names
print(class_names)

['airplane', 'automobile', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck']


## Data Augmentation

## Custom Model

In [12]:
def custom_model(input_shape, n_classes):
    input = keras.Input(shape=input_shape)
    x = keras.layers.Conv2D(32, (3,3), activation='relu', padding='same')(input)
    x = keras.layers.BatchNormalization()(x)
    x = keras.layers.Conv2D(32, (3, 3), activation='relu', padding='same')(x)
    x = keras.layers.BatchNormalization()(x)
    x = keras.layers.MaxPooling2D((2, 2))(x)

    x = keras.layers.Conv2D(64, (3, 3), activation='relu', padding='same')(x)
    x = keras.layers.BatchNormalization()(x)
    x = keras.layers.Conv2D(64, (3, 3), activation='relu', padding='same')(x)
    x = keras.layers.BatchNormalization()(x)
    x = keras.layers.MaxPooling2D((2, 2))(x)

    x = keras.layers.Conv2D(128, (3, 3), activation='relu', padding='same')(x)
    x = keras.layers.BatchNormalization()(x)
    x = keras.layers.Conv2D(128, (3, 3), activation='relu', padding='same')(x)
    x = keras.layers.BatchNormalization()(x)
    x = keras.layers.MaxPooling2D((2, 2))(x)

    x = keras.layers.Flatten()(x)
    x = keras.layers.Dropout(0.2)(x)

    # Hidden layer
    x = keras.layers.Dense(1024, activation='relu')(x)
    x = keras.layers.Dropout(0.2)(x)

    # last hidden layer i.e.. output layer
    x = keras.layers.Dense(n_classes, activation='softmax')(x)

    return keras.Model(input, x)



In [14]:
model = custom_model(input_shape=(32,32, 3), n_classes=10)

model.compile(
    optimizer=optimiser,  
    loss=loss_func,
    metrics=['accuracy']
)

In [22]:
model.history.history

{}

In [1]:
model.fit(
  train_ds,
  validation_data=validation_ds,
  epochs=nb_epochs
)

In [16]:
resultFile = []

total = 0
list = os.scandir(cinic_directory_test)
for testPicture in list:
    image_to_predict = cv2.imread(testPicture.path, cv2.IMREAD_COLOR)
    img_to_predict = np.expand_dims(cv2.resize(image_to_predict, (32, 32)), axis=0)
    
    #prediction
    res = np.argmax(model.predict(img_to_predict), axis=-1)
    resultFile.append(testPicture.name + ',' + class_names[res[0]])
    
    total += 1
    print("Total images : " + str(total), end='\r')
    # print(resultFile)
    
    
    
f = open(file_name, 'w')
f.write('filename,label')
f.write('\n')
for resultLine in resultFile:
    f.write(resultLine)
    f.write('\n')
f.close()

1/1 [==============================] - 0s 13ms/step


libpng warning: iCCP: profile 'ICC Profile': 'desc': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'wtpt': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'bkpt': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'rXYZ': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'gXYZ': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'bXYZ': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'dmnd': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'dmdd': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'vued': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'view': ICC profile tag start not a multiple of 4
libpng warning: iCCP: profile 'ICC Profile': 'lumi

1/1 [==============================] - 0s 13ms/step


libpng warning: iCCP: known incorrect sRGB profile


1/1 [==============================] - 0s 12ms/step


...

libpng warning: iCCP: known incorrect sRGB profile


1/1 [==============================] - 0s 13ms/step


libpng warning: iCCP: known incorrect sRGB profile
libpng warning: iCCP: known incorrect sRGB profile


1/1 [==============================] - 0s 12ms/step


libpng warning: iCCP: known incorrect sRGB profile
libpng warning: iCCP: known incorrect sRGB profile


In [26]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'

In [35]:
res = model.evaluate(validation_ds)

   6/1125 [..............................] - ETA: 30s - loss: 1.6229 - accuracy: 0.7083

2024-03-05 22:33:28.992857: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:28.996454: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:28.996701: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:28.997949: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:28.998274: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:28.999505: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:28.999549: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.003430: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: profile 'ICC Profile': 'desc': ICC profile tag start not a multiple of 4
2024-03-05 22:33:29.003574: 

  21/1125 [..............................] - ETA: 19s - loss: 1.6654 - accuracy: 0.6845

2024-03-05 22:33:29.213781: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.230430: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.242863: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.243573: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.256006: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.256781: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.283366: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.293400: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:29.293821: W tensorflow/core/lib/png/png_io.cc:88] PNG 

 154/1125 [===>..........................] - ETA: 14s - loss: 1.9984 - accuracy: 0.6834

...

1101/1125 [============================>.] - ETA: 0s - loss: 1.8236 - accuracy: 0.6927

2024-03-05 22:33:42.274274: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.286039: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.286544: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.296960: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.306901: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.307318: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.307762: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.317731: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.328711: W tensorflow/core/lib/png/png_io.cc:88] PNG 

1121/1125 [============================>.] - ETA: 0s - loss: 1.8198 - accuracy: 0.6928

2024-03-05 22:33:42.476661: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.478132: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.487292: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.487468: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.487830: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.488656: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.499285: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.500010: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile
2024-03-05 22:33:42.510406: W tensorflow/core/lib/png/png_io.cc:88] PNG 

1125/1125 [==============================] - 14s 12ms/step - loss: 1.8194 - accuracy: 0.6931


In [36]:
res

[1.8194164037704468, 0.6930555701255798]

In [37]:
from tensorflow.keras.applications import EfficientNetB0
import tensorflow as tf

In [38]:
model = EfficientNetB0(include_top=False, weights='imagenet')

16705208/16705208 [==============================] - 17s 1us/step
